In [2]:
import os
import sys
import datetime
from time import gmtime
from time import strftime
from pathlib import Path
from datetime import timedelta  
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
from scipy import signal
import pickle
import librosa
import librosa.display
#from utils_paper import data_ls_to_string, spectral_descriptors, spectral_subtraction, feature_extraction,extract_statistic, feature_selection, select_best_feature_selection_method, performance_on_selected_features, random_baseline_metrics, evaluate_model_performance, random_split_evaluation
from sklearn.model_selection import train_test_split
from feature_extraction import feature_extraction, extract_statistic

from regression_analysis import random_split_evaluation, independent_split_evaluation, random_baseline_metrics
from regression_analysis import evaluate_model_performance

import scipy
import scipy.signal
import scipy.fftpack


if not sys.warnoptions:
    import warnings
    warnings.simplefilter("ignore")

%load_ext autoreload
%autoreload 2


/opt/anaconda3/envs/conda_env_3_8/lib/python3.8/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


# Labels 2021

In [2]:
data = pd.read_csv("../data/annotations/inspections_2021.csv")
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 109 entries, 0 to 108
Data columns (total 12 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   Date             109 non-null    object 
 1   Tag number       109 non-null    int64  
 2   Colony Size      109 non-null    int64  
 3   Fob 1st          109 non-null    float64
 4   Fob 2nd          102 non-null    float64
 5   Fob 3rd          31 non-null     float64
 6   FoBrood          11 non-null     float64
 7   Queen status     108 non-null    object 
 8   Frames of Honey  63 non-null     float64
 9   Open             107 non-null    object 
 10  Close            107 non-null    object 
 11  Notes            64 non-null     object 
dtypes: float64(5), int64(2), object(5)
memory usage: 10.3+ KB


In [3]:
data = data.fillna(0)
data['Date'] = pd.to_datetime(data['Date'])
unique_hives = data['Tag number'].unique()
unique_hives

array([3629,    6, 3631, 3693, 3690, 3691, 3628, 3627, 3692, 3640])

In [4]:
grouped = data.groupby(['Tag number'])
dict_hives = {}
for i in unique_hives:
        dict_hives[i] = grouped.get_group(i)

In [5]:
for hive in  data['Tag number'].unique():
    dict_hives[hive] = dict_hives[hive].set_index(dict_hives[hive]['Date'])
    idx = pd.date_range(dict_hives[hive].index.min(), dict_hives[hive].index.max()+ timedelta(days=1), freq="15min")#  + timedelta(days=12)
    dict_hives[hive] = dict_hives[hive].reindex(idx)
    dict_hives[hive] = dict_hives[hive].drop(['Date'], axis=1)
    dict_hives[hive] = dict_hives[hive].interpolate(method="linear")#interpolate(method="ffill")
    dict_hives[hive]["fob"] = dict_hives[hive]["Fob 1st"] + dict_hives[hive]["Fob 2nd"]+ dict_hives[hive]["Fob 3rd"]
    dict_hives[hive]["fob"] = dict_hives[hive]["fob"]#.round(0).astype('f')

# Labels 2022

In [6]:
data_2022 = pd.read_csv("../data/annotations/inspections_2022.csv")
data_2022.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 288 entries, 0 to 287
Data columns (total 7 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Date           288 non-null    object 
 1   Tag number     288 non-null    int64  
 2   Category       274 non-null    object 
 3   Action detail  274 non-null    object 
 4   Queen status   278 non-null    object 
 5   Is alive       286 non-null    float64
 6   Report notes   183 non-null    object 
dtypes: float64(1), int64(1), object(5)
memory usage: 15.9+ KB


In [7]:
data_2022['Date'] = pd.to_datetime(data_2022['Date'], dayfirst=True).dt.date
data_2022 = data_2022.set_index('Date')

In [8]:
data_2022 = data_2022[data_2022['Category'] == 'frames of bees']
data_2022['Action detail'] = pd.to_numeric(data_2022['Action detail']) # conver the column from object to float
data_2022['Action detail'] = data_2022['Action detail'].astype('f') 

In [9]:
data_2022["fob"] = data_2022["Action detail"]

In [10]:
grouped = data_2022.groupby(['Tag number'])
dict_hives_2022 = {}
for i in data_2022['Tag number'].unique():
        dict_hives_2022[i] = grouped.get_group(i)

In [11]:
for hive in  data_2022['Tag number'].unique():
    idx = pd.date_range(dict_hives_2022[hive].index.min(), dict_hives_2022[hive].index.max() + timedelta (days=1), freq="15min")
    dict_hives_2022[hive] = dict_hives_2022[hive].reindex(idx)
    dict_hives_2022[hive] = dict_hives_2022[hive].interpolate(method="linear")#interpolate(method="ffill")
    dict_hives_2022[hive]['fob'] = dict_hives_2022[hive]['fob']#.round(0).astype('f')

# MFCCs

In [ ]:
hives = [6, 3627, 3628, 3629, 3631, 3640, 3690, 3691, 3692, 3693]

df = feature_extraction(feature='mfccs', sample_rate= 16000, n_fft = 1600,
                        hop_length = 800, dict_hives=dict_hives, hives=hives, year=2021, enhancement=False)
df.to_pickle("../data/features/2021_df_mfccs_win_" + str(win) +'_shift_' + str(shift) + "_n_filter_26.pkl")


In [ ]:
df = feature_extraction(feature='mfccs', sample_rate= 16000, n_fft = 1600,
                        hop_length = 800, dict_hives=dict_hives_2022, hives=hives, year=2022, enhancement=False)
df.to_pickle("../data/features/2022_df_mfccs_win_" + str(win) +'_shift_' + str(shift) +
             "_n_filter_26.pkl")


In [13]:
hives = [3691, 3692, 3693]

for hive in hives: 
    df = feature_extraction(feature='mfccs', sample_rate= 16000, n_fft = 1600,
                            hop_length = 800, dict_hives=dict_hives, hives=[hive], year=2021,  enhancement=True)
    df.to_pickle("../data/features/2021_df_ss_amp_mfccs_win_" + str(win) +'_shift_' + 
                 str(shift) +'_' + str(hive) + "_n_mels_26.pkl")
    

--------------------------------- // Hive number 3691 //---------- -------
-------------- ------------// File 12-08-2021_21h00_HIVE-3691.wav //------------- -------
Time taken for spectral subtraction for this file: 54.04209113121033 seconds
-------------- ------------// File 12-08-2021_21h30_HIVE-3691.wav //------------- -------
Time taken for spectral subtraction for this file: 61.81612515449524 seconds
-------------- ------------// File 12-08-2021_22h00_HIVE-3691.wav //------------- -------
Time taken for spectral subtraction for this file: 60.47761511802673 seconds
-------------- ------------// File 12-08-2021_22h30_HIVE-3691.wav //------------- -------
Time taken for spectral subtraction for this file: 63.52849102020264 seconds
-------------- ------------// File 12-08-2021_23h00_HIVE-3691.wav //------------- -------
Time taken for spectral subtraction for this file: 49.02196788787842 seconds
-------------- ------------// File 12-08-2021_23h30_HIVE-3691.wav //------------- -------


KeyboardInterrupt: 

In [ ]:
for hive in hives: 
    df = feature_extraction(feature='mfccs', sample_rate= 16000, n_fft = 1600,
                            hop_length = 800, dict_hives=dict_hives_2022, hives=[hive], year=2022,  enhancement=True)
    df.to_pickle("../data/features/2022_df_ss_amp_mfccs_win_" + str(win) +'_shift_' + str(shift) +'_' + str(hive) + "_n_mels_26.pkl")
    

# LFCC

In [21]:
hives = [6, 3627, 3628, 3629, 3631, 3640, 3690, 3691, 3692, 3693]
win=1600
shift=800

df = feature_extraction(feature='lfccs', sample_rate= 16000, n_fft = 1600,
                        hop_length = 800, dict_hives=dict_hives, hives=hives, year=2021, enhancement=False)
df.to_pickle("../data//features/2021_df_lfccs_win_" + str(win) +'_shift_' + str(shift) + "_n_filter_26.pkl")


--------------------------------- // Hive number 6 //---------- -------
-------------- ------------// File 11-08-2021_16h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_16h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_17h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_17h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_18h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_18h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_19h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_19h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_20h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_20h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_21h15_HIVE-6

-------------- ------------// File 13-08-2021_15h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_15h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_16h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_16h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_17h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_17h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_18h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_18h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_19h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_19h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_20h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-20

-------------- ------------// File 26-08-2021_06h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_07h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_07h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_08h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-20

-------------- ------------// File 16-09-2021_07h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_07h45_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_08h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_12h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-20

-------------- ------------// File 18-09-2021_06h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_07h15_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_07h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_08h15_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-20

...

-------------- ------------// File 20-09-2021_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_16h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_16h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_18h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_18h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_19h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_19h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_20h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 22-09-2021_13h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_13h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_14h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_14h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_16h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_16h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_18h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 24-09-2021_11h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_11h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_12h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_12h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_13h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_13h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_14h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_14h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_16h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 26-09-2021_09h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_09h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_10h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_10h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_11h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_11h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_12h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_12h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_13h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_13h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_14h00_HIVE-3693.wav //------------- -------
----------

NameError: name 'win' is not defined

In [25]:
df = feature_extraction(feature='lfccs', sample_rate= 16000, n_fft = 1600, hop_length = 800, dict_hives=dict_hives_2022, hives=hives, year=2022, enhancement=False)
df.to_pickle("../data/features/2022_df_lfccs_win_" + str(win) +'_shift_' + str(shift) + "_n_filter_26.pkl")


--------------------------------- // Hive number 6 //---------- -------
-------------- ------------// File 11-07-2022_04h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_05h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_05h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_06h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_06h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_07h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_07h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_08h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_08h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_09h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_09h30_HIVE-6

-------------- ------------// File 10-08-2022_18h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_18h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_19h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_19h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_20h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_20h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_21h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_21h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_22h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_22h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_23h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-20

-------------- ------------// File 19-08-2022_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_12h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_12h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_13h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_13h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_14h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-20

-------------- ------------// File 21-08-2022_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_12h15_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_12h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_13h15_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_13h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-20

-------------- ------------// File 23-08-2022_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_12h15_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_12h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_13h15_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_13h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-20

...

-------------- ------------// File 28-08-2022_10h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_11h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_11h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_12h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_12h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_13h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_13h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_14h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_14h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_15h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_16h15_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 30-08-2022_10h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_11h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_11h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_12h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_12h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_13h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_13h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_14h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_14h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_15h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_15h45_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 02-09-2022_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_18h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_18h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_19h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_19h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_20h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_20h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_21h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_21h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_22h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 04-09-2022_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_16h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_16h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_18h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_18h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_19h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_19h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_20h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 06-09-2022_13h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_13h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_14h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_14h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_15h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_15h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_16h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_16h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_17h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_17h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_18h15_HIVE-3693.wav //------------- -------
----------

In [ ]:
hives = [3627, 3628, 3629, 3631, 3640, 3690, 3691, 3692, 3693]

win=1600
shift=800

for hive in hives: 
    df = feature_extraction(feature='lfccs', sample_rate= 16000, n_fft = 1600,
                            hop_length = 800, dict_hives=dict_hives, hives=[hive], year=2021,  enhancement=True)
    df.to_pickle("../data/features/2021_df_ss_amp_lfccs_win_" + str(win) +'_shift_' +
                 str(shift) +'_' + str(hive) + "_n_mels_26.pkl")

--------------------------------- // Hive number 3627 //---------- -------
-------------- ------------// File 12-08-2021_17h15_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 14.193065166473389 seconds
-------------- ------------// File 12-08-2021_17h45_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 13.185733079910278 seconds
-------------- ------------// File 12-08-2021_18h00_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 16.75482201576233 seconds
-------------- ------------// File 12-08-2021_18h30_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 14.402667045593262 seconds
-------------- ------------// File 12-08-2021_19h00_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 12.789841890335083 seconds
-------------- ------------// File 12-08-2021_19h30_HIVE-3627.wav //------------- ----

Time taken for spectral subtraction for this file: 12.514297008514404 seconds
-------------- ------------// File 15-09-2021_04h30_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 12.377485990524292 seconds
-------------- ------------// File 15-09-2021_05h00_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 13.91734504699707 seconds
-------------- ------------// File 15-09-2021_05h30_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 13.373845100402832 seconds
-------------- ------------// File 15-09-2021_06h00_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 13.008808851242065 seconds
-------------- ------------// File 15-09-2021_06h30_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 12.867653131484985 seconds
-------------- ------------// File 15-09-2021_07h00_HIVE-3627.wav //------------- -

Time taken for spectral subtraction for this file: 12.615221977233887 seconds
-------------- ------------// File 16-09-2021_05h00_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 12.563214778900146 seconds
-------------- ------------// File 16-09-2021_05h30_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 12.447120904922485 seconds
-------------- ------------// File 16-09-2021_06h00_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 13.416047811508179 seconds
-------------- ------------// File 16-09-2021_06h30_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 13.577660083770752 seconds
-------------- ------------// File 16-09-2021_07h00_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 12.447631120681763 seconds
-------------- ------------// File 16-09-2021_07h30_HIVE-3627.wav //------------- 

Time taken for spectral subtraction for this file: 13.860300064086914 seconds
-------------- ------------// File 17-09-2021_05h30_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 12.288400888442993 seconds
-------------- ------------// File 17-09-2021_06h00_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 12.564115047454834 seconds
-------------- ------------// File 17-09-2021_06h30_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 12.569825172424316 seconds
-------------- ------------// File 17-09-2021_07h00_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 12.618911981582642 seconds
-------------- ------------// File 17-09-2021_07h30_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 14.091569900512695 seconds
-------------- ------------// File 17-09-2021_08h00_HIVE-3627.wav //------------- 

Time taken for spectral subtraction for this file: 13.311710834503174 seconds
-------------- ------------// File 18-09-2021_06h00_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 13.346038818359375 seconds
-------------- ------------// File 18-09-2021_06h30_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 11.986860990524292 seconds
-------------- ------------// File 18-09-2021_07h00_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 12.038545846939087 seconds
-------------- ------------// File 18-09-2021_07h30_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 12.34696102142334 seconds
-------------- ------------// File 18-09-2021_08h00_HIVE-3627.wav //------------- -------
Time taken for spectral subtraction for this file: 12.351263999938965 seconds
-------------- ------------// File 18-09-2021_08h30_HIVE-3627.wav //------------- -

...

-------------- ------------// File 18-09-2021_23h45_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 13.528556108474731 seconds
-------------- ------------// File 19-09-2021_00h15_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 14.131417989730835 seconds
-------------- ------------// File 19-09-2021_00h45_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 14.844186067581177 seconds
-------------- ------------// File 19-09-2021_01h15_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 16.481804132461548 seconds
-------------- ------------// File 19-09-2021_01h45_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 13.956286907196045 seconds
-------------- ------------// File 19-09-2021_02h15_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 14.386651992797852 

-------------- ------------// File 14-10-2021_09h15_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 15.341857194900513 seconds
-------------- ------------// File 14-10-2021_09h45_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 15.982054948806763 seconds
-------------- ------------// File 14-10-2021_10h15_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 14.897246360778809 seconds
-------------- ------------// File 14-10-2021_10h45_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 14.84089708328247 seconds
-------------- ------------// File 14-10-2021_11h15_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 14.664277791976929 seconds
-------------- ------------// File 14-10-2021_11h45_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 15.930129766464233 s

-------------- ------------// File 15-10-2021_09h45_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 16.17531394958496 seconds
-------------- ------------// File 15-10-2021_10h15_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 15.738741636276245 seconds
-------------- ------------// File 15-10-2021_10h45_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 13.4654381275177 seconds
-------------- ------------// File 15-10-2021_11h15_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 13.835109949111938 seconds
-------------- ------------// File 15-10-2021_11h45_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 13.644265174865723 seconds
-------------- ------------// File 15-10-2021_12h15_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 15.450019836425781 sec

-------------- ------------// File 16-10-2021_10h15_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 19.292330026626587 seconds
-------------- ------------// File 16-10-2021_10h45_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 20.349921226501465 seconds
-------------- ------------// File 16-10-2021_11h15_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 18.522655963897705 seconds
-------------- ------------// File 16-10-2021_11h45_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 17.788411140441895 seconds
-------------- ------------// File 16-10-2021_12h15_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 19.79491686820984 seconds
-------------- ------------// File 16-10-2021_12h45_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 18.257370710372925 s

-------------- ------------// File 17-10-2021_10h45_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 16.736965894699097 seconds
-------------- ------------// File 17-10-2021_11h15_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 17.65599274635315 seconds
-------------- ------------// File 17-10-2021_11h45_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 17.377453088760376 seconds
-------------- ------------// File 17-10-2021_12h15_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 18.78131103515625 seconds
-------------- ------------// File 17-10-2021_12h45_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 20.0584979057312 seconds
-------------- ------------// File 17-10-2021_13h15_HIVE-3692.wav //------------- -------
Time taken for spectral subtraction for this file: 14.79243803024292 secon

In [ ]:
hives = [6, 3627, 3628, 3629, 3631, 3640, 3690, 3691, 3692, 3693]

for hive in hives: 
    df = feature_extraction(feature='lfccs', sample_rate= 16000, n_fft = 1600,
                            hop_length = 800, dict_hives=dict_hives_2022, hives=[hive], year=2022,  enhancement=True)
    df.to_pickle("../data/features/2022_df_ss_amp_lfccs_win_" + str(win) +'_shift_' +
                 str(shift) +'_' + str(hive) + "_n_mels_26.pkl")
    

# Spectral features

In [26]:
hives = [6, 3627, 3628, 3629, 3631, 3640, 3690, 3691, 3692, 3693]


df = feature_extraction(feature='spectral_shape_descriptors', sample_rate= 16000, n_fft = 1600,
                        hop_length = 800, dict_hives=dict_hives, hives=hives, year=2021, enhancement=False)
df.to_pickle("../data/features/2021_df_spectral_nine_features.pkl")


--------------------------------- // Hive number 6 //---------- -------
-------------- ------------// File 11-08-2021_16h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_16h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_17h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_17h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_18h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_18h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_19h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_19h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_20h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_20h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_21h15_HIVE-6

-------------- ------------// File 13-08-2021_15h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_15h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_16h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_16h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_17h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_17h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_18h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_18h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_19h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_19h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_20h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-20

-------------- ------------// File 26-08-2021_06h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_07h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_07h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_08h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-20

-------------- ------------// File 16-09-2021_07h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_07h45_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_08h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_12h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-20

-------------- ------------// File 18-09-2021_06h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_07h15_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_07h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_08h15_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-20

...

-------------- ------------// File 18-09-2021_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_18h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_18h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_19h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_19h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_20h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_20h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_21h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_21h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_22h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 20-09-2021_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_16h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_16h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_18h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_18h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_19h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_19h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_20h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 22-09-2021_13h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_13h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_14h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_14h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_16h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_16h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_18h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 24-09-2021_11h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_11h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_12h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_12h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_13h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_13h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_14h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_14h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_16h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 26-09-2021_09h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_09h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_10h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_10h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_11h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_11h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_12h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_12h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_13h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_13h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_14h00_HIVE-3693.wav //------------- -------
----------

In [27]:
df = feature_extraction(feature='spectral_shape_descriptors', sample_rate= 16000, n_fft = 1600,
                        hop_length = 800, dict_hives=dict_hives_2022, hives=hives, year=2022, enhancement=False)
df.to_pickle("../data/features/2022_df_spectral_nine_features.pkl")


--------------------------------- // Hive number 6 //---------- -------
-------------- ------------// File 11-07-2022_04h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_05h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_05h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_06h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_06h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_07h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_07h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_08h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_08h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_09h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_09h30_HIVE-6

-------------- ------------// File 10-08-2022_18h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_18h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_19h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_19h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_20h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_20h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_21h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_21h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_22h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_22h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_23h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-20

-------------- ------------// File 19-08-2022_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_12h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_12h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_13h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_13h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_14h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-20

-------------- ------------// File 21-08-2022_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_12h15_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_12h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_13h15_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_13h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-20

-------------- ------------// File 23-08-2022_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_12h15_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_12h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_13h15_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_13h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-20

...

-------------- ------------// File 28-08-2022_10h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_11h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_11h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_12h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_12h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_13h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_13h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_14h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_14h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_15h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_16h15_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 30-08-2022_10h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_11h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_11h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_12h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_12h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_13h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_13h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_14h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_14h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_15h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_15h45_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 02-09-2022_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_18h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_18h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_19h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_19h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_20h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_20h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_21h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_21h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_22h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 04-09-2022_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_16h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_16h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_18h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_18h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_19h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_19h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_20h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 06-09-2022_13h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_13h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_14h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_14h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_15h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_15h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_16h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_16h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_17h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_17h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_18h15_HIVE-3693.wav //------------- -------
----------

In [ ]:
for hive in hives: 
    df = feature_extraction(feature='spectral_shape_descriptors', sample_rate= 16000, n_fft = 1600,
                            hop_length = 800, dict_hives=dict_hives_2021, hives=[hive], year=2021,  enhancement=True)
    df.to_pickle("../data/features/2021_df_ss_amp_spectral_nine_features_" + str(hive) + ".pkl")
    

In [ ]:
for hive in hives: 
    df = feature_extraction(feature='spectral_shape_descriptors', sample_rate= 16000, n_fft = 1600,
                            hop_length = 800, dict_hives=dict_hives_2022, hives=[hive], year=2022,  enhancement=True)
    df.to_pickle("../data/features/2022_df_ss_amp_spectral_nine_features_" + str(hive) + ".pkl")
    

# Hand crafted features

In [28]:
df = feature_extraction(feature='nectar_hand_crafted', sample_rate= 15625, n_fft=512,
                        hop_length=512, dict_hives=dict_hives, hives=hives, year=2021, enhancement=False)
df.to_pickle("../data/features/2021_df_nectar_features.pkl")



--------------------------------- // Hive number 6 //---------- -------
-------------- ------------// File 11-08-2021_16h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_16h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_17h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_17h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_18h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_18h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_19h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_19h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_20h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_20h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_21h15_HIVE-6

-------------- ------------// File 13-08-2021_15h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_15h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_16h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_16h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_17h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_17h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_18h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_18h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_19h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_19h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_20h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-20

-------------- ------------// File 26-08-2021_06h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_07h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_07h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_08h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-20

-------------- ------------// File 16-09-2021_07h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_07h45_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_08h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-2021_12h15_HIVE-6.wav //------------- -------
-------------- ------------// File 16-09-20

-------------- ------------// File 18-09-2021_06h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_07h15_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_07h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_08h15_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-2021_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 18-09-20

...

-------------- ------------// File 18-09-2021_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_18h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_18h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_19h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_19h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_20h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_20h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_21h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_21h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 18-09-2021_22h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 20-09-2021_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_16h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_16h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_18h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_18h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_19h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_19h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 20-09-2021_20h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 22-09-2021_13h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_13h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_14h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_14h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_16h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_16h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_18h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 24-09-2021_11h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_11h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_12h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_12h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_13h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_13h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_14h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_14h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_16h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 26-09-2021_09h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_09h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_10h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_10h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_11h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_11h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_12h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_12h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_13h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_13h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_14h00_HIVE-3693.wav //------------- -------
----------

In [29]:
df = feature_extraction(feature='nectar_hand_crafted', sample_rate= 15625, n_fft=512,
                        hop_length=512, dict_hives=dict_hives_2022, hives=hives, year=2022, enhancement=False)
df.to_pickle("../data/features/2022_df_nectar_features.pkl")


--------------------------------- // Hive number 6 //---------- -------
-------------- ------------// File 11-07-2022_04h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_05h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_05h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_06h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_06h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_07h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_07h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_08h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_08h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_09h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_09h30_HIVE-6

-------------- ------------// File 10-08-2022_18h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_18h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_19h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_19h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_20h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_20h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_21h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_21h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_22h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_22h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_23h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-20

-------------- ------------// File 19-08-2022_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_12h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_12h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_13h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_13h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_14h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-20

-------------- ------------// File 21-08-2022_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_12h15_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_12h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_13h15_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-2022_13h45_HIVE-6.wav //------------- -------
-------------- ------------// File 21-08-20

-------------- ------------// File 23-08-2022_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_12h15_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_12h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_13h15_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-2022_13h45_HIVE-6.wav //------------- -------
-------------- ------------// File 23-08-20

...

-------------- ------------// File 28-08-2022_10h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_11h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_11h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_12h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_12h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_13h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_13h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_14h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_14h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_15h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 28-08-2022_16h15_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 30-08-2022_10h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_11h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_11h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_12h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_12h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_13h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_13h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_14h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_14h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_15h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 30-08-2022_15h45_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 02-09-2022_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_18h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_18h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_19h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_19h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_20h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_20h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_21h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_21h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 02-09-2022_22h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 04-09-2022_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_16h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_16h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_18h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_18h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_19h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_19h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 04-09-2022_20h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 06-09-2022_13h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_13h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_14h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_14h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_15h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_15h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_16h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_16h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_17h15_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_17h45_HIVE-3693.wav //------------- -------
-------------- ------------// File 06-09-2022_18h15_HIVE-3693.wav //------------- -------
----------

In [41]:
for hive in hives: 
    df = feature_extraction(feature='nectar_hand_crafted', sample_rate= 15625, n_fft=512,
                            hop_length=512, dict_hives=dict_hives, hives=[hive], year=2021, enhancement=True)
    df.to_pickle("../data/features/2021_df_ss_amp_hand_crafted_" + str(hive) + ".pkl")
    

--------------------------------- // Hive number 6 //---------- -------
-------------- ------------// File 11-08-2021_16h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_16h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_16h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_16h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_17h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_17h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_17h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_17h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_18h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_18h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2021_18h45_HIVE-6

-------------- ------------// File 12-08-2021_15h45_HIVE-6.wav //------------- -------
-------------- ------------// File 12-08-2021_15h45_HIVE-6.wav //------------- -------
-------------- ------------// File 12-08-2021_16h15_HIVE-6.wav //------------- -------
-------------- ------------// File 12-08-2021_16h15_HIVE-6.wav //------------- -------
-------------- ------------// File 12-08-2021_16h45_HIVE-6.wav //------------- -------
-------------- ------------// File 12-08-2021_16h45_HIVE-6.wav //------------- -------
-------------- ------------// File 12-08-2021_17h15_HIVE-6.wav //------------- -------
-------------- ------------// File 12-08-2021_17h15_HIVE-6.wav //------------- -------
-------------- ------------// File 12-08-2021_17h45_HIVE-6.wav //------------- -------
-------------- ------------// File 12-08-2021_17h45_HIVE-6.wav //------------- -------
-------------- ------------// File 12-08-2021_18h15_HIVE-6.wav //------------- -------
-------------- ------------// File 12-08-20

-------------- ------------// File 13-08-2021_15h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_15h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_15h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_16h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_16h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_16h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_16h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_17h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_17h15_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_17h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-2021_17h45_HIVE-6.wav //------------- -------
-------------- ------------// File 13-08-20

-------------- ------------// File 25-08-2021_07h15_HIVE-6.wav //------------- -------
-------------- ------------// File 25-08-2021_07h15_HIVE-6.wav //------------- -------
-------------- ------------// File 25-08-2021_07h45_HIVE-6.wav //------------- -------
-------------- ------------// File 25-08-2021_07h45_HIVE-6.wav //------------- -------
-------------- ------------// File 25-08-2021_08h15_HIVE-6.wav //------------- -------
-------------- ------------// File 25-08-2021_08h15_HIVE-6.wav //------------- -------
-------------- ------------// File 25-08-2021_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 25-08-2021_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 25-08-2021_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 25-08-2021_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 25-08-2021_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 25-08-20

-------------- ------------// File 26-08-2021_06h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_07h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_07h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_07h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_07h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_08h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_08h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_08h45_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-2021_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 26-08-20

...

-------------- ------------// File 22-09-2021_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_16h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_16h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_16h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_16h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_17h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_18h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 22-09-2021_18h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 23-09-2021_14h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 23-09-2021_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 23-09-2021_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 23-09-2021_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 23-09-2021_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 23-09-2021_16h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 23-09-2021_16h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 23-09-2021_16h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 23-09-2021_16h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 23-09-2021_17h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 23-09-2021_17h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 24-09-2021_13h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_14h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_14h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_14h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_14h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_15h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_16h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 24-09-2021_16h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 25-09-2021_12h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 25-09-2021_13h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 25-09-2021_13h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 25-09-2021_13h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 25-09-2021_13h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 25-09-2021_14h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 25-09-2021_14h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 25-09-2021_14h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 25-09-2021_14h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 25-09-2021_15h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 25-09-2021_15h00_HIVE-3693.wav //------------- -------
----------

-------------- ------------// File 26-09-2021_11h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_12h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_12h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_12h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_12h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_13h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_13h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_13h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_13h30_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_14h00_HIVE-3693.wav //------------- -------
-------------- ------------// File 26-09-2021_14h00_HIVE-3693.wav //------------- -------
----------

In [ ]:
for hive in hives: 
    df = feature_extraction(feature='nectar_hand_crafted', sample_rate= 15625, n_fft=512,
                            hop_length=512, dict_hives=dict_hives_2022, hives=[hive], year=2022, enhancement=True)
    df.to_pickle("../data/features/2022_df_ss_amp_hand_crafted_" + str(hive) + ".pkl")
    

--------------------------------- // Hive number 6 //---------- -------
-------------- ------------// File 11-07-2022_04h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_04h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_05h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_05h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_05h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_05h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_06h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_06h00_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_06h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_06h30_HIVE-6.wav //------------- -------
-------------- ------------// File 11-07-2022_07h00_HIVE-6

-------------- ------------// File 12-07-2022_04h30_HIVE-6.wav //------------- -------
-------------- ------------// File 12-07-2022_04h30_HIVE-6.wav //------------- -------
-------------- ------------// File 12-07-2022_05h00_HIVE-6.wav //------------- -------
-------------- ------------// File 12-07-2022_05h00_HIVE-6.wav //------------- -------
-------------- ------------// File 12-07-2022_05h30_HIVE-6.wav //------------- -------
-------------- ------------// File 12-07-2022_05h30_HIVE-6.wav //------------- -------
-------------- ------------// File 12-07-2022_06h00_HIVE-6.wav //------------- -------
-------------- ------------// File 12-07-2022_06h00_HIVE-6.wav //------------- -------
-------------- ------------// File 12-07-2022_06h30_HIVE-6.wav //------------- -------
-------------- ------------// File 12-07-2022_06h30_HIVE-6.wav //------------- -------
-------------- ------------// File 12-07-2022_07h00_HIVE-6.wav //------------- -------
-------------- ------------// File 12-07-20

-------------- ------------// File 10-08-2022_18h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_18h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_18h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_19h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_19h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_19h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_19h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_20h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_20h15_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_20h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-2022_20h45_HIVE-6.wav //------------- -------
-------------- ------------// File 10-08-20

-------------- ------------// File 11-08-2022_18h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2022_18h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2022_18h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2022_18h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2022_19h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2022_19h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2022_19h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2022_19h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2022_20h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2022_20h15_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-2022_20h45_HIVE-6.wav //------------- -------
-------------- ------------// File 11-08-20

-------------- ------------// File 19-08-2022_09h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_09h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_10h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_10h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_11h15_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-2022_11h45_HIVE-6.wav //------------- -------
-------------- ------------// File 19-08-20

...

-------------- ------------// File 31-08-2022_01h15_HIVE-6.wav //------------- -------
-------------- ------------// File 31-08-2022_01h15_HIVE-6.wav //------------- -------
-------------- ------------// File 31-08-2022_01h45_HIVE-6.wav //------------- -------
-------------- ------------// File 31-08-2022_01h45_HIVE-6.wav //------------- -------
-------------- ------------// File 31-08-2022_02h15_HIVE-6.wav //------------- -------
-------------- ------------// File 31-08-2022_02h15_HIVE-6.wav //------------- -------
-------------- ------------// File 31-08-2022_02h45_HIVE-6.wav //------------- -------
-------------- ------------// File 31-08-2022_02h45_HIVE-6.wav //------------- -------
-------------- ------------// File 31-08-2022_03h15_HIVE-6.wav //------------- -------
-------------- ------------// File 31-08-2022_03h15_HIVE-6.wav //------------- -------
-------------- ------------// File 31-08-2022_03h45_HIVE-6.wav //------------- -------
-------------- ------------// File 31-08-20

-------------- ------------// File 01-09-2022_00h45_HIVE-6.wav //------------- -------
-------------- ------------// File 01-09-2022_01h15_HIVE-6.wav //------------- -------
-------------- ------------// File 01-09-2022_01h15_HIVE-6.wav //------------- -------
-------------- ------------// File 01-09-2022_01h45_HIVE-6.wav //------------- -------
-------------- ------------// File 01-09-2022_01h45_HIVE-6.wav //------------- -------
-------------- ------------// File 01-09-2022_02h30_HIVE-6.wav //------------- -------
-------------- ------------// File 01-09-2022_02h30_HIVE-6.wav //------------- -------
-------------- ------------// File 01-09-2022_03h00_HIVE-6.wav //------------- -------
-------------- ------------// File 01-09-2022_03h00_HIVE-6.wav //------------- -------
-------------- ------------// File 01-09-2022_03h30_HIVE-6.wav //------------- -------
-------------- ------------// File 01-09-2022_03h30_HIVE-6.wav //------------- -------
-------------- ------------// File 01-09-20

-------------- ------------// File 02-09-2022_01h30_HIVE-6.wav //------------- -------
-------------- ------------// File 02-09-2022_01h30_HIVE-6.wav //------------- -------
-------------- ------------// File 02-09-2022_02h00_HIVE-6.wav //------------- -------
-------------- ------------// File 02-09-2022_02h00_HIVE-6.wav //------------- -------
-------------- ------------// File 02-09-2022_02h30_HIVE-6.wav //------------- -------
-------------- ------------// File 02-09-2022_02h30_HIVE-6.wav //------------- -------
-------------- ------------// File 02-09-2022_03h00_HIVE-6.wav //------------- -------
-------------- ------------// File 02-09-2022_03h00_HIVE-6.wav //------------- -------
-------------- ------------// File 02-09-2022_03h30_HIVE-6.wav //------------- -------
-------------- ------------// File 02-09-2022_03h30_HIVE-6.wav //------------- -------
-------------- ------------// File 02-09-2022_04h00_HIVE-6.wav //------------- -------
-------------- ------------// File 02-09-20

-------------- ------------// File 03-09-2022_01h30_HIVE-6.wav //------------- -------
-------------- ------------// File 03-09-2022_02h00_HIVE-6.wav //------------- -------
-------------- ------------// File 03-09-2022_02h00_HIVE-6.wav //------------- -------
-------------- ------------// File 03-09-2022_02h30_HIVE-6.wav //------------- -------
-------------- ------------// File 03-09-2022_02h30_HIVE-6.wav //------------- -------
-------------- ------------// File 03-09-2022_03h00_HIVE-6.wav //------------- -------
-------------- ------------// File 03-09-2022_03h00_HIVE-6.wav //------------- -------
-------------- ------------// File 03-09-2022_03h30_HIVE-6.wav //------------- -------
-------------- ------------// File 03-09-2022_03h30_HIVE-6.wav //------------- -------
-------------- ------------// File 03-09-2022_04h00_HIVE-6.wav //------------- -------
-------------- ------------// File 03-09-2022_04h00_HIVE-6.wav //------------- -------
-------------- ------------// File 03-09-20

-------------- ------------// File 04-09-2022_01h30_HIVE-6.wav //------------- -------
-------------- ------------// File 04-09-2022_01h30_HIVE-6.wav //------------- -------
-------------- ------------// File 04-09-2022_02h00_HIVE-6.wav //------------- -------
-------------- ------------// File 04-09-2022_02h00_HIVE-6.wav //------------- -------
-------------- ------------// File 04-09-2022_02h30_HIVE-6.wav //------------- -------
-------------- ------------// File 04-09-2022_02h30_HIVE-6.wav //------------- -------
-------------- ------------// File 04-09-2022_03h00_HIVE-6.wav //------------- -------
-------------- ------------// File 04-09-2022_03h00_HIVE-6.wav //------------- -------
-------------- ------------// File 04-09-2022_03h30_HIVE-6.wav //------------- -------
-------------- ------------// File 04-09-2022_03h30_HIVE-6.wav //------------- -------
-------------- ------------// File 04-09-2022_04h00_HIVE-6.wav //------------- -------


# Extract statistic

In [41]:
win = 1600
shift= 800

mfccs_2021 = pd.read_pickle("../data/features/2021_df_mfccs_win_" + str(win) +'_shift_' + str(shift) + "_n_mels_26.pkl")
mfccs_2022 = pd.read_pickle("../data/features/2022_df_mfccs_win_" + str(win) +'_shift_' + str(shift) + "_n_mels_26.pkl")


mfccs_2021['date'] = pd.to_datetime(mfccs_2021['date'], dayfirst=True)
mfccs_2021 = mfccs_2021.set_index(mfccs_2021['date'])
mfccs_2021 = mfccs_2021.drop(['date'], axis=1)

mfccs_2022['date'] = pd.to_datetime(mfccs_2022['date'], dayfirst=True)
mfccs_2022 = mfccs_2022.set_index(mfccs_2022['date'])
mfccs_2022 = mfccs_2022.drop(['date'], axis=1)

mfccs_feature_2021 = extract_statistic(mfccs_2021, mfccs_2021.columns[3:], 2021, '00:00', '23:00');
mfccs_feature_2022 = extract_statistic(mfccs_2022, mfccs_2022.columns[3:], 2022, '00:00', '23:00');
mfccs_features = pd.concat([mfccs_feature_2021, mfccs_feature_2022])

6.0
3627.0
3628.0
3631.0
3640.0
3690.0
3691.0
3692.0
3693.0
6.0
3627.0
3628.0
3631.0
3640.0
3690.0
3691.0
3692.0
3693.0


In [12]:
win = 1600
shift= 800

lfccs_2021 = pd.read_pickle("../data/features/2021_df_lfccs_win_" + str(win) +'_shift_' + str(shift) + "_n_filter_26.pkl")
lfccs_2022 = pd.read_pickle("../data/features/2022_df_lfccs_win_" + str(win) +'_shift_' + str(shift) + "_n_filter_26.pkl")


lfccs_2021['date'] = pd.to_datetime(lfccs_2021['date'], dayfirst=True)
lfccs_2021 = lfccs_2021.set_index(lfccs_2021['date'])
lfccs_2021 = lfccs_2021.drop(['date'], axis=1)

lfccs_2022['date'] = pd.to_datetime(lfccs_2022['date'], dayfirst=True)
lfccs_2022 = lfccs_2022.set_index(lfccs_2022['date'])
lfccs_2022 = lfccs_2022.drop(['date'], axis=1)

lfccs_feature_2021 = extract_statistic(lfccs_2021, lfccs_2021.columns[3:],  2021, '00:00', '23:00');
lfccs_feature_2022 = extract_statistic(lfccs_2022, lfccs_2022.columns[3:], 2022, '00:00', '23:00');
lfccs_features = pd.concat([lfccs_feature_2021, lfccs_feature_2022])

6.0
3627.0
3628.0
3631.0
3640.0
3690.0
3691.0
3692.0
3693.0
6.0
3627.0
3628.0
3631.0
3640.0
3690.0
3691.0
3692.0
3693.0


In [14]:
spectral_2021 = pd.read_pickle("../data/features/2021_df_spectral_nine_features.pkl")
spectral_2022 = pd.read_pickle("../data/features/2022_df_spectral_nine_features.pkl")

spectral_2021['date'] = pd.to_datetime(spectral_2021['date'], dayfirst=True)
spectral_2021 = spectral_2021.set_index(spectral_2021['date'])
spectral_2021 = spectral_2021.drop(['date'], axis=1)

spectral_2022['date'] = pd.to_datetime(spectral_2022['date'], dayfirst=True)
spectral_2022 = spectral_2022.set_index(spectral_2022['date'])
spectral_2022 = spectral_2022.drop(['date'], axis=1)

spectral_feature_2021 = extract_statistic(spectral_2021, ['centroid', 'spread', 'skewness', 'kurtosis', 'flatness', 'rolloff', 'crest','flux', 'entropy'], 2021, '00:00', '23:00')
spectral_feature_2022 = extract_statistic(spectral_2022, ['centroid', 'spread', 'skewness', 'kurtosis', 'flatness', 'rolloff', 'crest','flux', 'entropy'], 2022, '00:00', '23:00')
spectral_features = pd.concat([spectral_feature_2021, spectral_feature_2022])

6.0
3627.0
3628.0
3631.0
3640.0
3690.0
3691.0
3692.0
3693.0
6.0
3627.0
3628.0
3631.0
3640.0
3690.0
3691.0
3692.0
3693.0


In [52]:
hand_crafted_2021 = pd.read_pickle("../data/features/2021_df_hand_crafted_features.pkl")
hand_crafted_2022 = pd.read_pickle("../data/features/2022_df_hand_crafted_features.pkl")

hand_crafted_2021['date'] = pd.to_datetime(hand_crafted_2021['date'], dayfirst=True)
hand_crafted_2021 = hand_crafted_2021.set_index(hand_crafted_2021['date'])
hand_crafted_2021 = hand_crafted_2021.drop(['date'], axis=1)

hand_crafted_2022['date'] = pd.to_datetime(hand_crafted_2022['date'], dayfirst=True)
hand_crafted_2022 = hand_crafted_2022.set_index(hand_crafted_2022['date'])
hand_crafted_2022 = hand_crafted_2022.drop(['date'], axis=1)

hand_crafted_feature_2021 = extract_statistic(hand_crafted_2021, hand_crafted_2021.columns[3:], 2021, '00:00', '23:00')
hand_crafted_feature_2022 = extract_statistic(hand_crafted_2022, hand_crafted_2022.columns[3:], 2022, '00:00', '23:00')
hand_crafted_features = pd.concat([hand_crafted_feature_2021, hand_crafted_feature_2022])

6.0
3627.0
3628.0
3631.0
3640.0
3690.0
3691.0
3692.0
3693.0
6.0
3627.0
3628.0
3631.0
3640.0
3690.0
3691.0
3692.0
3693.0


In [48]:
win = 1600
shift= 800

hives = [6, 3627, 3628, 3629, 3631, 3640, 3690, 3691, 3692, 3693]

    
mfccs_ss_2021=pd.concat(
        [pd.read_pickle(f"../data/features/{2021}_df_ss_amp_mfccs_win_{win}_shift_{shift}_{hive}_n_mels_26.pkl") 
         for hive in hives],
        ignore_index=True)


mfccs_ss_2021['date'] = pd.to_datetime(mfccs_ss_2021['date'], dayfirst=True)
mfccs_ss_2021 = mfccs_ss_2021.set_index(mfccs_ss_2021['date'])
mfccs_ss_2021 = mfccs_ss_2021.drop(['date'], axis=1)

mfccs_ss_2022=pd.concat(
        [pd.read_pickle(f"../data/features/{2022}_df_ss_amp_mfccs_win_{win}_shift_{shift}_{hive}_n_mels_26.pkl") 
         for hive in hives],
        ignore_index=True)


mfccs_ss_2022['date'] = pd.to_datetime(mfccs_ss_2022['date'], dayfirst=True)
mfccs_ss_2022 = mfccs_ss_2022.set_index(mfccs_ss_2022['date'])
mfccs_ss_2022 = mfccs_ss_2022.drop(['date'], axis=1)


mfccs_ss_feature_2021 = extract_statistic(mfccs_ss_2021, mfccs_ss_2021.columns[3:], 2021, '00:00', '23:00');
mfccs_ss_feature_2022 = extract_statistic(mfccs_ss_2022, mfccs_ss_2022.columns[3:], 2022, '00:00', '23:00');
mfccs_ss_features = pd.concat([mfccs_ss_feature_2021, mfccs_ss_feature_2022])



FileNotFoundError: [Errno 2] No such file or directory: '../data/Nectar/features/2022_df_ss_amp_mfccs_win_1600_shift_800_3628_n_mels_26.pkl'

In [ ]:
win = 1600
shift= 800

hives = [6, 3627, 3628, 3629, 3631, 3640, 3690, 3691, 3692, 3693]

    
lfccs_ss_2021=pd.concat(
        [pd.read_pickle(f"../data/features/{2021}_df_ss_amp_lfccs_win_{win}_shift_{shift}_{hive}_n_mels_26.pkl") 
         for hive in hives],
        ignore_index=True)

lfccs_ss_2021['date'] = pd.to_datetime(lfccs_ss_2021['date'], dayfirst=True)
lfccs_ss_2021 = lfccs_ss_2021.set_index(lfccs_ss_2021['date'])
lfccs_ss_2021 = lfccs_ss_2021.drop(['date'], axis=1)

lfccs_ss_2022=pd.concat(
        [pd.read_pickle(f"../data/features/{2022}_df_ss_amp_lfccs_win_{win}_shift_{shift}_{hive}_n_mels_26.pkl") 
         for hive in hives],
        ignore_index=True)


lfccs_ss_2022['date'] = pd.to_datetime(lfccs_ss_2022['date'], dayfirst=True)
lfccs_ss_2022 = lfccs_ss_2022.set_index(lfccs_ss_2022['date'])
lfccs_ss_2022 = lfccs_ss_2022.drop(['date'], axis=1)



lfccs_ss_feature_2021 = extract_statistic(lfccs_ss_2021, lfccs_ss_2021.columns[3:],  2021, '00:00', '23:00');
lfccs_ss_feature_2022 = extract_statistic(lfccs_ss_2022, lfccs_ss_2022.columns[3:], 2022, '00:00', '23:00');
lfccs_ss_feature = pd.concat([lfccs_ss_feature_2021, lfccs_ss_feature_2022])


In [56]:

hives = [6, 3627, 3628, 3629, 3631, 3640, 3690, 3691, 3692, 3693]

    
spectral_ss_2021=pd.concat(
        [pd.read_pickle(f"../data/features/{2021}_df_ss_amp_spectral_nine_features_" + str(hive) + ".pkl") 
         for hive in hives],
        ignore_index=True)

spectral_ss_2021['date'] = pd.to_datetime(spectral_ss_2021['date'], dayfirst=True)
spectral_ss_2021 = spectral_ss_2021.set_index(spectral_ss_2021['date'])
spectral_ss_2021 = spectral_ss_2021.drop(['date'], axis=1)

spectral_ss_2022=pd.concat(
        [pd.read_pickle(f"../data/features/{2022}_df_ss_amp_spectral_nine_features_" + str(hive) + ".pkl") 
         for hive in hives],
        ignore_index=True)


spectral_ss_2022['date'] = pd.to_datetime(spectral_ss_2022['date'], dayfirst=True)
spectral_ss_2022 = spectral_ss_2022.set_index(spectral_ss_2022['date'])
spectral_ss_2022 = spectral_ss_2022.drop(['date'], axis=1)

spectral_ss_feature_2021 = extract_statistic(spectral_ss_2021, spectral_ss_2021.columns[3:],  2021, '00:00', '23:00');
spectral_ss_feature_2022 = extract_statistic(spectral_ss_2022, spectral_ss_2022.columns[3:], 2022, '00:00', '23:00');
spectral_ss_feature = pd.concat([spectral_ss_feature_2021, spectral_ss_feature_2022])


FileNotFoundError: [Errno 2] No such file or directory: '../data/Nectar/features/2021_df_ss_amp_spectral_nine_features_6.pkl'

In [55]:

hives = [6, 3627, 3628, 3629, 3631, 3640, 3690, 3691, 3692, 3693]

    
hand_crafted_ss_2021=pd.concat(
        [pd.read_pickle(f"../data/features/{2021}_df_ss_amp_hand_crafted_" + str(hive) + ".pkl") 
         for hive in hives],
        ignore_index=True)

hand_crafted_ss_2021['date'] = pd.to_datetime(hand_crafted_ss_2021['date'], dayfirst=True)
hand_crafted_ss_2021 = hand_crafted_ss_2021.set_index(hand_crafted_ss_2021['date'])
hand_crafted_ss_2021 = hand_crafted_ss_2021.drop(['date'], axis=1)

hand_crafted_ss_2022=pd.concat(
        [pd.read_pickle(f"../data/features/{2022}_df_ss_amp_hand_crafted_" + str(hive) + ".pkl") 
         for hive in hives],
        ignore_index=True)


hand_crafted_ss_2022['date'] = pd.to_datetime(hand_crafted_ss_2022['date'], dayfirst=True)
hand_crafted_ss_2022 = hand_crafted_ss_2022.set_index(hand_crafted_ss_2022['date'])
hand_crafted_ss_2022 = hand_crafted_ss_2022.drop(['date'], axis=1)

hand_crafted_ss_feature_2021 = extract_statistic(hand_crafted_ss_2021, hand_crafted_ss_2021.columns[3:],  2021, '00:00', '23:00');
hand_crafted_ss_feature_2022 = extract_statistic(hand_crafted_ss_2022, hand_crafted_ss_2022.columns[3:], 2022, '00:00', '23:00');
hand_crafted_ss_feature = pd.concat([hand_crafted_ss_feature_2021, hand_crafted_ss_feature_2022])


6.0
3627.0
3628.0
3631.0
3640.0
3690.0
3691.0
3692.0
3693.0
6.0
3627.0
3628.0
3631.0
3640.0
3690.0
3691.0
3692.0
3693.0


# Repeat 10 times - Random-split

In [42]:
feature = 'mfccs' #nectar, mfccs, lfccs, spectral
feature_data = mfccs_features # nectar_features, lfccs_features, mfccs_features, spectral_features 

In [ ]:
model_predictions, y_tests = random_split_evaluation(feature_data, feature=feature, n_iterations=10,
                                                     model='random forest')


Index(['mean_mfccs_9'], dtype='object')
Index(['mean_mfccs_9', 'mean_mfccs_2'], dtype='object')
Index(['mean_mfccs_9', 'mean_mfccs_2', 'mean_mfccs_11'], dtype='object')
Index(['mean_mfccs_9', 'mean_mfccs_2', 'mean_mfccs_11', 'mean_mfccs_4'], dtype='object')


In [ ]:
random_predictions = random_baseline_metrics(y_tests, n_iterations=10, random_range=(0, 31))


In [ ]:
results = evaluate_model_performance(y_tests, random_predictions, model_predictions)


# Repeat 10 times - Independent-split

In [ ]:
feature = 'mfccs' #hand_crafted, mfccs, lfccs, spectral
feature_data = mfccs_features # hand_crafted_features, lfccs_features, mfccs_features, spectral_features 

In [ ]:
initial_train_hives = [3628, 3631, 6, 3640, 3693] 
initial_test_hives = [3692, 3690]
initial_val_hives = [3691, 3627]

model_predictions, y_tests = independent_split_evaluation(feature_data, feature=feature,
                                                          initial_train_hives, initial_val_hives,
                                                          initial_test_hives, n_iterations=10,
                                                          model='random forest')

In [ ]:
random_predictions = random_baseline_metrics(y_tests, n_iterations=10, random_range=(0, 31))


In [ ]:
results = evaluate_model_performance(y_tests, random_predictions, model_predictions)
